# Juliaで信号処理の練習
## オーディオデータを取り扱う

オーディオファイルのIO，再生，編集，録音とか

次のパッケージを使用する  
[SampledSignals.jl](https://github.com/JuliaAudio/SampledSignals.jl)　ファイルから読み込んだ/録音したオーディオデータを保持する構造体が定義されている  
[LibSndFile.jl](https://github.com/JuliaAudio/SampledSignals.jl)　オーディオファイルIO．wav，mp3，FLAC等いろいろ読める．  
[PortAudio.jl](https://github.com/JuliaAudio/PortAudio.jl)　マイク入力を録音したり，処理したり．  

### 1. Julia上で生成した波形データの音を聞く

In [1]:
using SampledSignals

In [2]:
#サンプリングレート48 kHzで周波数440 Hzのサイン波 2秒分のデータを用意
fs = 48000.0
n = [i for i in 0:96000]
wavedata = sin.(2π*440.0*n/fs)

#生成したデータからSampleBufインスタンスを生成
buf = SampleBuf(wavedata, fs)

96001-frame, 1-channel SampleBuf{Float64, 1}
2.000020833333333s sampled at 48000.0Hz
████████████████████████████████████████████████████████████████████████████████

SampleBuf構造体がオーディオデータを保持する．  
SampleBuf.samplerate，SampleBuf.dataとして，サンプルレート，オーディオデータを保持．  
オーディオデータの振幅は，[-1.0, 1.0]の範囲（正確には1.0は含まれないが詳細は省略)．|1.0|より大きいとクリップ．  
**SampleBufインスタンスをCellの出力にすると，Jupyter上ですぐに音を聞くことができる**

In [3]:
#ステレオも可能
#サンプルデータ*チャンネルつまりWaveLength*2の行列からSampleBufを作ればOK
leftwave = wavedata
rightwave = 0.2*wavedata
stereodata = [leftwave rightwave]
stereobuf = SampleBuf(stereodata, fs)

96001-frame, 2-channel SampleBuf{Float64, 2}
2.000020833333333s sampled at 48000.0Hz
████████████████████████████████████████████████████████████████████████████████
▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆▆

### 2. オーディオファイルを読み込んで再生する

In [4]:
using LibSndFile

In [5]:
drumloop = load("./Resource/AudioSample.wav")
@show typeof(drumloop)
drumloop

typeof(drumloop) = SampledSignals.SampleBuf{FixedPointNumbers.Fixed{Int16,15},2}


480000-frame, 2-channel SampleBuf{FixedPointNumbers.Fixed{Int16,15}, 2}
10.0s sampled at 48000.0Hz
▆▃▃▂▆▄▄▂▆▃▆▃▆▄▄▂▆▃▃▂▆▄▄▂▆▃▆▃▆▄▆▃▆▃▃▂▆▄▄▂▆▃▆▃▆▄▄▂▆▃▃▂▆▄▄▂▆▃▆▃▆▄▆▃▂▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁
▆▃▃▁▆▄▄▂▆▃▆▃▆▄▄▂▆▃▃▂▆▄▃▂▆▃▆▃▆▄▆▃▆▃▃▁▆▄▄▂▆▃▆▃▆▄▄▂▆▃▃▂▆▄▃▂▆▃▆▃▆▄▆▃▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁

読み込んだオーディオファイルのデータはSampleBufインスタンスとして返される  
従って，Jupyter上ですぐに再生可能

### 3. オーディオデータを編集する

先のドラムループの左チャンネルだけをノーマライズしてみる

In [6]:
stereodrum = convert(Array{Float64}, drumloop.data)

480000×2 Array{Float64,2}:
  0.000244141   0.000335693
  0.000732422   0.000854492
  0.00131226    0.00152588 
  0.00338745    0.00366211 
  0.00619507    0.00646973 
  0.00479126    0.00509644 
 -0.00363159   -0.0032959  
 -0.0126038    -0.0122375  
 -0.0128784    -0.0123901  
 -0.00317383   -0.00265503 
  0.00912476    0.00970459 
  0.0169373     0.0175781  
  0.0152283     0.0159912  
  ⋮                        
  0.0           0.0        
  3.05176e-5    3.05176e-5 
 -3.05176e-5   -3.05176e-5 
  3.05176e-5    3.05176e-5 
  0.0           0.0        
  0.0           0.0        
  0.0           0.0        
  0.0           0.0        
  3.05176e-5    3.05176e-5 
  0.0           0.0        
  0.0           0.0        
  0.0           0.0        

オーディオフィルから読んだデータは，[FixedPointNumbers.Fixed型](https://github.com/JuliaMath/FixedPointNumbers.jl)  
小数点以下の桁数が固定された小数（らしい）  
そのまま，Float32/64と混ぜて計算できるけど，一応，先に型変換しておく

In [7]:
leftdata = stereodrum[:, 1]
rightdata = stereodrum[:, 2]
maxval, minval = extrema(leftdata)
normalizeco = maximum([abs(maxval), abs(minval)])
leftdata = leftdata/normalizeco
normalizeddata = [leftdata rightdata]
normalizeddrum = SampleBuf(normalizeddata, drumloop.samplerate)

480000-frame, 2-channel SampleBuf{Float64, 2}
10.0s sampled at 48000.0Hz
▇▅▅▃▇▅▅▃▇▄▇▄▇▆▅▃▇▄▅▃▇▅▅▃▇▅▇▄█▅▇▄▇▅▅▃▇▅▅▃▇▄▇▄▇▆▅▃▇▄▅▃▇▅▅▃▇▅▇▄█▅▇▄▃▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁
▆▃▃▁▆▄▄▂▆▃▆▃▆▄▄▂▆▃▃▂▆▄▃▂▆▃▆▃▆▄▆▃▆▃▃▁▆▄▄▂▆▃▆▃▆▄▄▂▆▃▃▂▆▄▃▂▆▃▆▃▆▄▆▃▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁

（そういえば，組み込みのnormalize関数があったか...？）

### 4. マイクから録音する
**これ以降のコードは，nbviewer上だと動作しないのでローカルで試してみてください**

In [8]:
using PortAudio

LoadError: InitError: [91mMethodError: no method matching redirect_stderr(::IJulia.IJuliaStdio{Base.PipeEndpoint})[0m
Closest candidates are:
  redirect_stderr() at stream.jl:1034
  redirect_stderr([91m::Union{Base.LibuvStream, IOStream}[39m) at stream.jl:1028
  redirect_stderr([91m::Function[39m, [91m::Any[39m) at stream.jl:1082[39m
during initialization of module PortAudio

jupyter上だとusing PortAudio時にエラー吐くけど，今のところ録音時に問題は確認できてないのでこのまま続けます．  
外付けAudio IFに使われているASIOドライバ等は認識できないので，Audio IFを使っている人は既定の録音・再生デバイスをデフォルトのサウンドカードにしておいてください．

In [ ]:
stream = PortAudio.PortAudioStream(1, 0)

1in/0outのストリームを作成．（とりあえず録音だけなので）．
マイク入力を拾えるようになる

In [10]:
#このCellを実行すると5秒間マイクの音を録音開始
#録音データはSampleBufインスタンスとして返ってくるので，再生プレイヤーが立ち上がる
recbuf = read(stream, 5s)

220500-frame, 1-channel SampleBuf{Float32, 2}
5.0s sampled at 44100.0Hz
▁▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▅▇▄▄▅▇▄▅▇▇▃▃▇▇

### 5. マイクからひろった音をリアルタイムで処理して，スピーカーに出力

In [11]:
stream = PortAudio.PortAudioStream(1, 1, synced=true)
@show stream.blocksize

stream.blocksize = 4096


4096

1in/1outのストリームを作成．synced=trueで入出力バッファの同期がとれる．

In [12]:
#マイク入力にリアルタイムでトレモロをかけてみる
L = stream.blocksize
fs = stream.samplerate
n = 0
for i in 1:100
    #blocksize分の入力サンプルを処理して出力するという操作を繰り返す(=blocksize * 100 / fs秒分行う)
    inbuff = read(stream, L)
    audiodata = convert(Array{Float32}, inbuff.data[:, 1])
    
    for j in 1:L
        audiodata[j] = audiodata[j]*sin(2π*5.0*n/fs)
        n += 1
    end
    
    outbuff = SampledSignals.SampleBuf(audiodata, fs)
    write(stream, outbuff, L)
end